In [1]:
import re
from bs4 import BeautifulSoup
import requests
import html5lib
import json

In [2]:
url = 'https://www.cna.com.tw/list/aspt.aspx'
res = requests.get(url)
soup = BeautifulSoup(res.text,'html5lib')
n=0
labels=[]
while n < len(soup.select_one('#pnProductNavContents > ul').findAll('li')):
    try :
        lab = soup.select_one('#pnProductNavContents > ul').findAll('li')[n].find('a',{'class':'first-level'}).text
        url =soup.select_one('#pnProductNavContents > ul').findAll('li')[n].find('a',{'class':'first-level'})['href']
    except:(TypeError,IndentationError)
    labels.append((url,lab))
    n += 1
labels = list(set(labels))
labels.remove(('http://cnavideo.cna.com.tw', '影音'))
labels.remove(('/list/aall.aspx', '即時'))
labels.append(('https://www.cna.com.tw/list/aall.aspx', '即時'))
#labels.remove(('https://www.cna.com.tw/keyword/九合一.aspx', '九合一'))
labels.remove(('https://www.cna.com.tw/list/sp.aspx', '專題'))
labels.remove(('https://www.cna.com.tw/list/aall.aspx', '即時'))

labs = []
for item in labels:
    item = [item[0],item[1]]

    item[0] = re.search(r'list\/\w+',item[0]).group()[5:]
    labs.append(item)

In [3]:
def payload(item):
    payload={
        'id': '1056893641102242',
    'ev': 'Microdata',
    'dl': item[0],
    'rl': 'https://www.cna.com.tw/',
    'if': 'false',
    'ts': '1541087113735',
    'cd[Schema.org]': [],
    #'cd[OpenGraph]': {"og:url":"https://www.cna.com.tw/list/ahel.aspx","og:title":"生活 | 中央社 CNA","og:description":"想知道統一發票、大樂透、威力彩開獎號碼、各種醫療保健、交通氣象、颱風動態等生活資訊，及升學考試、教育政策、課綱改革等文教訊息，通通都在中央社生活新聞。","og:image:height":"200","og:image:width":"200","og:image":"https://img5.cna.com.tw/www/images/pic_fb.jpg","og:type":"article","article:author":"https://www.facebook.com/cnanewstaiwan","article:publisher":"https://www.facebook.com/cnanewstaiwan"}
    #'cd[Meta]': {"title":"\n\t生活 | 中央社 CNA\n","meta:description":"想知道統一發票、大樂透、威力彩開獎號碼、各種醫療保健、交通氣象、颱風動態等生活資訊，及升學考試、教育政策、課綱改革等文教訊息，通通都在中央社生活新聞。","meta:keywords":"News, 新聞, 即時新聞, 中央社"}
    'cd[DataLayer]': [],
    'cd[JSON-LD]': [],
    'sw': '1280',
    'sh': '5000',#'720',
    'v': '2.8.30',
    'r': 'stable',
    'a': 'tmgoogletagmanager',
    'ec': '1',
    'o': '30',
    'fbp': 'fb.2.1541074934894.620990608',
    'it': '1541087112886',
    'coo': 'false',
    'es': 'automatic',
    }
    return payload

In [4]:
labs_href=[]
for item in labs:
    soups=[]
    n=1
    while n < 13:
        url = 'https://www.cna.com.tw/cna2018api/api/simplelist/categorycode/'+item[0]+'/pageidx/'+str(n)
        res = requests.get(url)
        soup = BeautifulSoup(res.text,'html5lib')
        body = soup.findAll('body')[0].getText()
        PageUrl = re.findall(r'\"PageUrl\"\:\S[^\,]+',body)
        urls = [txt[11:-1] for txt in PageUrl]
        soups.extend(urls)
        n += 1
        if len(urls) < 20:
            break
    labs_href.append([soups,item[1]])

In [5]:
news={}
newslist=[]
for lab in labs_href:
    lab_name = lab[1]
    lab_urls = lab[0]
    n = 0
    for url in lab_urls:
        res = requests.get(url)
        soup = BeautifulSoup(res.text,'html5lib')
        txt = ""
        try:
            title = soup.find_all('div',{'class':'centralContent'})[0].find_all('h1')[0].getText()
            for s in soup.find_all('div',{'class':'paragraph'})[0].findAll('p'):
                txt=txt+s.getText()
        except:IndexError
        research = re.search(r'[\）\)\：\:\》](.+[\。\!\?\s])+',txt)
        if research == None or len(research.group())<2:
            print(txt)
        else:
            txt = re.search(r'[\）\)\：\:\》](.+[\。\!\?\s])+',txt).group()[1:]

        page = [[title,txt],lab_name]
        newslist.append(page)
        news[(title,txt)]=lab_name
        n += 1
        if n % 20 == 0:
            print((lab_name,n),end=",")

('文化', 20),('文化', 40),('文化', 60),('文化', 80),('文化', 100),('科技', 20),('科技', 40),('科技', 60),('科技', 80),('科技', 100),('政治', 20),('政治', 40),('政治', 60),('政治', 80),('政治', 100),('國際', 20),('國際', 40),('國際', 60),('國際', 80),('國際', 100),('產經', 20),('產經', 40),('產經', 60),('產經', 80),('產經', 100),('社會', 20),('社會', 40),('社會', 60),('社會', 80),('社會', 100),('證券', 20),('證券', 40),('證券', 60),('證券', 80),('證券', 100),('娛樂', 20),('娛樂', 40),('娛樂', 60),('娛樂', 80),('娛樂', 100),('兩岸', 20),中央社駐上海特派員陳家倫/1月10日現年92歲的上海海關大鐘近來開始誤點，去年8月還一度中暑暈厥了好幾小時。衰老的大鐘預計於今年接受英國原廠「健檢」，不論結果是搶救或無痛地走向終點，都將轟動上海灘。上海海關大樓是外灘知名歷史建築，頂部的大鐘與倫敦大笨鐘是「姊妹」，由英國同一家公司生產。據稱，上海海關大鐘當年總造價高達5000多兩白銀，於1927年8月從倫敦運到上海，原包裝木箱連同大鐘重達6.25噸。1928年元旦凌晨1時，海關大鐘敲響了第一聲，從此以後，鐘聲就日以繼夜地陪伴著上海人。對於早年生活並不富裕的中國民眾而言，別說手上戴個表，連在家掛個時鐘都是奢侈，噹噹響的鐘聲因而成了市民珍視的「公共財」。「以前再遠都聽得到呦」，62歲的上海徐姓民眾從小在靜安寺附近長大，住家距離外灘約5公里遠。他回憶，學齡前就對海關大鐘的鐘聲有印象，但受到都市化的高樓阻絕、汽車雜音干擾，老家現已聽不到鐘聲。至於原先住在外灘一帶的居民，因都市計畫與拆遷的關係，也從海關大鐘的「搖滾區」撤出，接替而上的是大批境外觀光客，連帶將海關大鐘推向世界，鐘聲敲進了更多人的耳裡，並迴盪在老上海的記憶中。享受世人矚目的同時，邁入92歲的海關大鐘也面臨著歲月的考驗，自去年起，就開始不太準時，常有熱心民眾去電通報

In [6]:
import jieba
import nltk

In [7]:
stopwords=[]
with open('../30/txt/stopwords_ch.txt', 'r', encoding='UTF-8') as file:
    for data in file.readlines():
        data = data.strip()
        stopwords.append(data)

In [8]:
lab_tags ={}
prelab = ''
books = list(news.items())
for book in books:
    for lab in ['生活','運動','政治','科技','國際','兩岸','產經','社會','地方','娛樂','證券','文化']:
        if book[1]==lab:
            if prelab != lab:
                txt=''
            txt = txt+book[0][1]
            lab_tags[book[1]] = txt
            prelab = lab

In [86]:
filterwords=[
    '年','月','中央社','記者','編輯','譯者','日電'
    ,'\n',' ','「','」','『','』'
    ,'今天','說','表示','年','月','日','後','前','時','應','中','今年'
    ,'兩','下','人','最','次','再','先','盡量'
]

In [10]:
articles = []
for news in newslist:
    articles.append((news[0][1],news[1]))
    

In [13]:
books = []


for n in range(len(articles)):

    txt_dic = {}
    txt = articles[n]
    txt_dic[txt[0]] = txt[1]
    books.append(txt_dic)


In [57]:
def get_tags(books=books):
    tags = {}  
    labs = list(set([v for b in books for v in b.values()]))
    for lab in labs:
        txt = ""
        for book in books:
            if list(book.values())[0] == lab:
                txt += list(book.keys())[0]
        tags[lab] = txt
    return tags

In [60]:
txt_tags = get_tags(books)

In [70]:
txt_tags

{'兩岸': "中國駐美大使崔天凱今天闡述中國國家主席習近平的對台談話時表示，希望美方支持中國的台灣議題主張，恪守一個中國原則與中美三個聯合公報精神，慎重妥善處理涉台議題。中國駐美大使館今天傍晚在使館舉辦習近平對台談話座談會。崔天凱表示和平統一、一國兩制是實現國家統一的最佳法案，強調兩岸同胞是一家人，兩岸的事是兩岸同胞家裡的事，「得要家裡人商量著辦」。他對習近平提到不放棄武力犯台的說法指出，不承諾放棄使用武力，針對的是外部勢力干涉，以及極少數台獨分裂分子和其分裂活動，「中國人的事由中國人決定」，台灣問題事關中國核心利益和中國人民民族情感，是中國內政，不容外來干涉。崔天凱指出，今年是「告台灣同胞書」發表40週年，也是中美建交40週年。40年來，台灣問題始終是中美關係中最重要、最敏感的核心問題。經驗表明，台灣問題處理得好，中美關係發展就會更加順暢，反之就會遭遇波折。他表示，中美聯合三公報構成中美關係最為重要的政治文件，也是過去40多年來，中美關係發展的根本依據。當前中美關係再次處於關鍵發展階段，中國願與美方一起按照中美兩國元首在阿根廷會晤達成的重要共識，共同推進以協調、合作、穩定為基調的中美關係。崔天凱特別呼籲美方，希望美國尊重中國的核心利益與中國人民的民族情感，支持中國在新時代台灣問題的政治主張，恪守一個中國原則與中美三公報精神，慎重妥善處理涉台問題，以實際行動維護中美關係大局與台海和平穩定。他表示，希望兩岸青年團結友愛、攜手打拚，共同追夢、築夢、圓夢，希望大家共同為探索「一國兩制」台灣方案貢獻智慧。習近平2日在「告台灣同胞書」40週年發表談話時提出探索兩制的台灣方案，和平統一、一國兩制是實現國家統一的最佳方式，還提出在九二共識基礎上，兩岸各政黨、各界推舉代表性人士，就兩岸關係和民族未來開展廣泛深入的民主協商。總統蔡英文也在2日發表談話回應指出，不接受九二共識，根本原因就是北京當局所定義的九二共識，其實就是「一個中國」、「一國兩制」，並重申台灣絕不會接受「一國兩制」，絕大多數台灣民意也堅決反對「一國兩制」，這也是「台灣共識」。港媒報導，正在赤柱監獄服刑的香港前行政長官（特首）曾蔭權，昨天因為身體不適被送到醫院治療。他預定15日刑滿出獄。曾蔭權因為「公職人員行為失當罪」成立而被判入獄20個月，正在赤柱監獄服刑。綜合本地電子媒體今天報導，曾蔭權11日感到不適而被送院治療。

In [111]:
def get_fwords(txt="",top=300,twotop = 20,output_values='items'):
    seg_list = jieba.cut(txt, cut_all=False)
    txt = ",".join(seg_list)
    tokens = txt.split(',')

    tokens = [re.match(r'\w+',w).group() for w in tokens if (w not in stopwords and w not in filterwords) and re.match(r'\w+',w) != None]
#    tokens = list(filter(lambda a: a not in stopwords and a not in filterwords and a.isalpha() == True,tokens))#and len(a)>1, tokens))
    one = nltk.FreqDist(tokens).most_common(top)
    
    ###
    lab_alltwowords = list(nltk.bigrams(tokens))
    two = [(str(i[0][0])+str(i[0][1]),i[1]) for i in nltk.FreqDist(lab_alltwowords).most_common(twotop)]

    ###
    wordcount_dict = {}
    for com in [two,one]:
        for i in com:
            if re.search(r'\D+',i[0]) != None:
                wordcount_dict[i[0]] = i[1]
    if output_values == 'items':
        return list(wordcount_dict.items())
    elif output_values == 'dic':
        return wordcount_dict

In [125]:
def get_fwords_tags(output_values='items'):
    
    fwords_tags = {}
    for i in list(txt_tags.items()):
        fwords_tags[i[0]]=get_fwords(i[1],top=300,output_values=output_values) 
    return fwords_tags

In [126]:
fwords_tags_items = get_fwords_tags(output_values='items')

In [127]:
fwords_tags_dic = get_fwords_tags(output_values='dic')

In [128]:
fwords_tags_dic

{'兩岸': {'40週年': 16,
  'iPhone': 16,
  '一國兩制': 94,
  '一國兩制台灣': 13,
  '上海': 54,
  '上述': 17,
  '下降': 17,
  '中共': 59,
  '中國': 397,
  '中國人': 17,
  '中國國家': 26,
  '中國大陸': 54,
  '中央': 42,
  '中小學': 19,
  '中小學教師': 14,
  '中心': 36,
  '中美': 25,
  '主席': 27,
  '主席習近平': 13,
  '主張': 20,
  '主教': 15,
  '主權': 21,
  '主義': 18,
  '主要': 26,
  '九二': 68,
  '九二共識': 68,
  '事': 14,
  '事件': 16,
  '些': 28,
  '交流': 16,
  '人口': 27,
  '人員': 48,
  '人士': 24,
  '人民幣': 29,
  '代表': 25,
  '令': 17,
  '以上': 15,
  '企業': 31,
  '伊斯蘭教': 18,
  '位': 20,
  '低': 16,
  '作出': 19,
  '作戰': 15,
  '做': 16,
  '價格': 16,
  '億': 26,
  '億元': 20,
  '元': 79,
  '兆': 16,
  '內容': 33,
  '全國': 23,
  '全球': 17,
  '兩岸': 72,
  '公共': 16,
  '公司': 44,
  '公布': 25,
  '公開': 16,
  '共同': 24,
  '共識': 90,
  '出現': 16,
  '分析': 22,
  '利益': 14,
  '制度': 27,
  '副': 18,
  '副中心': 17,
  '加強': 17,
  '包括': 42,
  '北京': 144,
  '北京市': 19,
  '北京方面': 34,
  '協商': 14,
  '協會': 17,
  '占': 17,
  '印象': 15,
  '卻': 17,
  '原則': 20,
  '去年': 65,
  '參加': 22,
  '反對': 14,
  '召開': 20,
  '台': 50,


In [121]:
fwords_tags_items

{'兩岸': [('九二共識', 68),
  ('中國大陸', 54),
  ('蔡總統', 37),
  ('北京方面', 34),
  ('中國國家', 26),
  ('億元', 20),
  ('經濟成長', 18),
  ('副中心', 17),
  ('台灣同胞書', 16),
  ('40週年', 16),
  ('告台灣', 15),
  ('行政長官', 14),
  ('中小學教師', 14),
  ('教師資格', 14),
  ('國家主席', 13),
  ('主席習近平', 13),
  ('國家統一', 13),
  ('一國兩制台灣', 13),
  ('總統蔡英文', 13),
  ('中國', 397),
  ('台灣', 239),
  ('香港', 202),
  ('北京', 144),
  ('報導', 125),
  ('國家', 123),
  ('大陸', 107),
  ('一國兩制', 94),
  ('共識', 90),
  ('指出', 87),
  ('習近平', 84),
  ('元', 79),
  ('已', 77),
  ('政府', 76),
  ('兩岸', 72),
  ('九二', 68),
  ('經濟', 68),
  ('去年', 65),
  ('民主', 62),
  ('提出', 60),
  ('美國', 59),
  ('中共', 59),
  ('總統', 57),
  ('認為', 56),
  ('工作', 55),
  ('名', 54),
  ('上海', 54),
  ('新', 53),
  ('接受', 52),
  ('方面', 51),
  ('進行', 51),
  ('台', 50),
  ('問題', 50),
  ('關係', 49),
  ('人員', 48),
  ('大學', 48),
  ('發展', 47),
  ('城市', 47),
  ('會議', 46),
  ('統一', 45),
  ('發表', 45),
  ('市場', 45),
  ('相關', 45),
  ('公司', 44),
  ('包括', 42),
  ('中央', 42),
  ('國歌', 42),
  ('政策', 41),
  ('委員會', 41

In [184]:
def remove_mix(fword_value="items",lab_fwords={}):

    dic3={}
    for lab in lab_fwords.keys():   
        word_content2 = lab_fwords[lab].copy()
        if fword_value == "dic":
            word_content2 = list(word_content2.items())
#        print(word_content2)
        for lab2 in lab_fwords.keys():    
            if lab != lab2:
                if fword_value == "items":
                    word_content = [w for w in lab_fwords[lab] if (w[0] in [a[0] for a in lab_fwords[lab2]])]
                    for w in word_content:
                        try:
                            word_content2.remove(w)                  
                        except ValueError:
                            pass
            if fword_value == "items":
                dic3[lab] = word_content2 
            if fword_value == "dic":
                ddd = {}
                for i in word_content2:
                    ddd[i[0]]=i[1]
                dic3[lab] = ddd

    """    elif fword_value == "dic":
        print(lab_fwords[lab].items())
        word_content = [w for w in lab_fwords[lab].items() if (w in [a for a in lab_fwords[lab2].items()])]
        for w in word_content:
            try:
                word_content2.remove(w)                  
            except ValueError:
                pass"""
    

    return dic3

In [115]:
txt_tags

{'兩岸': "中國駐美大使崔天凱今天闡述中國國家主席習近平的對台談話時表示，希望美方支持中國的台灣議題主張，恪守一個中國原則與中美三個聯合公報精神，慎重妥善處理涉台議題。中國駐美大使館今天傍晚在使館舉辦習近平對台談話座談會。崔天凱表示和平統一、一國兩制是實現國家統一的最佳法案，強調兩岸同胞是一家人，兩岸的事是兩岸同胞家裡的事，「得要家裡人商量著辦」。他對習近平提到不放棄武力犯台的說法指出，不承諾放棄使用武力，針對的是外部勢力干涉，以及極少數台獨分裂分子和其分裂活動，「中國人的事由中國人決定」，台灣問題事關中國核心利益和中國人民民族情感，是中國內政，不容外來干涉。崔天凱指出，今年是「告台灣同胞書」發表40週年，也是中美建交40週年。40年來，台灣問題始終是中美關係中最重要、最敏感的核心問題。經驗表明，台灣問題處理得好，中美關係發展就會更加順暢，反之就會遭遇波折。他表示，中美聯合三公報構成中美關係最為重要的政治文件，也是過去40多年來，中美關係發展的根本依據。當前中美關係再次處於關鍵發展階段，中國願與美方一起按照中美兩國元首在阿根廷會晤達成的重要共識，共同推進以協調、合作、穩定為基調的中美關係。崔天凱特別呼籲美方，希望美國尊重中國的核心利益與中國人民的民族情感，支持中國在新時代台灣問題的政治主張，恪守一個中國原則與中美三公報精神，慎重妥善處理涉台問題，以實際行動維護中美關係大局與台海和平穩定。他表示，希望兩岸青年團結友愛、攜手打拚，共同追夢、築夢、圓夢，希望大家共同為探索「一國兩制」台灣方案貢獻智慧。習近平2日在「告台灣同胞書」40週年發表談話時提出探索兩制的台灣方案，和平統一、一國兩制是實現國家統一的最佳方式，還提出在九二共識基礎上，兩岸各政黨、各界推舉代表性人士，就兩岸關係和民族未來開展廣泛深入的民主協商。總統蔡英文也在2日發表談話回應指出，不接受九二共識，根本原因就是北京當局所定義的九二共識，其實就是「一個中國」、「一國兩制」，並重申台灣絕不會接受「一國兩制」，絕大多數台灣民意也堅決反對「一國兩制」，這也是「台灣共識」。港媒報導，正在赤柱監獄服刑的香港前行政長官（特首）曾蔭權，昨天因為身體不適被送到醫院治療。他預定15日刑滿出獄。曾蔭權因為「公職人員行為失當罪」成立而被判入獄20個月，正在赤柱監獄服刑。綜合本地電子媒體今天報導，曾蔭權11日感到不適而被送院治療。

In [185]:
remove_mix(lab_fwords=fwords_tags_dic,fword_value='dic')

{'兩岸': {'40週年': 16,
  'iPhone': 16,
  '一國兩制': 94,
  '一國兩制台灣': 13,
  '上海': 54,
  '上述': 17,
  '下降': 17,
  '中共': 59,
  '中國': 397,
  '中國人': 17,
  '中國國家': 26,
  '中國大陸': 54,
  '中央': 42,
  '中小學': 19,
  '中小學教師': 14,
  '中心': 36,
  '中美': 25,
  '主席': 27,
  '主席習近平': 13,
  '主張': 20,
  '主教': 15,
  '主權': 21,
  '主義': 18,
  '主要': 26,
  '九二': 68,
  '九二共識': 68,
  '事': 14,
  '事件': 16,
  '些': 28,
  '交流': 16,
  '人口': 27,
  '人員': 48,
  '人士': 24,
  '人民幣': 29,
  '代表': 25,
  '令': 17,
  '以上': 15,
  '企業': 31,
  '伊斯蘭教': 18,
  '位': 20,
  '低': 16,
  '作出': 19,
  '作戰': 15,
  '做': 16,
  '價格': 16,
  '億': 26,
  '億元': 20,
  '元': 79,
  '兆': 16,
  '內容': 33,
  '全國': 23,
  '全球': 17,
  '兩岸': 72,
  '公共': 16,
  '公司': 44,
  '公布': 25,
  '公開': 16,
  '共同': 24,
  '共識': 90,
  '出現': 16,
  '分析': 22,
  '利益': 14,
  '制度': 27,
  '副': 18,
  '副中心': 17,
  '加強': 17,
  '包括': 42,
  '北京': 144,
  '北京市': 19,
  '北京方面': 34,
  '協商': 14,
  '協會': 17,
  '占': 17,
  '印象': 15,
  '卻': 17,
  '原則': 20,
  '去年': 65,
  '參加': 22,
  '反對': 14,
  '召開': 20,
  '台': 50,


In [186]:
remove_mix(lab_fwords=fwords_tags_items,fword_value='items')

{'兩岸': [('中國大陸', 54),
  ('北京方面', 34),
  ('經濟成長', 18),
  ('副中心', 17),
  ('台灣同胞書', 16),
  ('40週年', 16),
  ('告台灣', 15),
  ('行政長官', 14),
  ('中小學教師', 14),
  ('教師資格', 14),
  ('國家統一', 13),
  ('一國兩制台灣', 13),
  ('中共', 59),
  ('上海', 54),
  ('統一', 45),
  ('國歌', 42),
  ('教師', 30),
  ('立法會', 30),
  ('泛民', 29),
  ('官方', 28),
  ('人口', 27),
  ('制度', 27),
  ('運動', 26),
  ('新疆', 24),
  ('堅持', 23),
  ('資格', 22),
  ('部門', 22),
  ('教育營', 22),
  ('意見', 21),
  ('主權', 21),
  ('展振振', 21),
  ('普選', 21),
  ('主張', 20),
  ('原則', 20),
  ('週年', 20),
  ('居民', 20),
  ('稱', 20),
  ('學員', 20),
  ('作出', 19),
  ('中小學', 19),
  ('就業', 19),
  ('北京市', 19),
  ('大鐘', 19),
  ('退學', 19),
  ('實現', 18),
  ('指', 18),
  ('副', 18),
  ('產生', 18),
  ('伊斯蘭教', 18),
  ('中國人', 17),
  ('上述', 17),
  ('法律', 17),
  ('下降', 17),
  ('告', 16),
  ('同胞書', 16),
  ('領導', 16),
  ('近日', 16),
  ('國務院', 16),
  ('市委', 16),
  ('政協', 16),
  ('深圳', 16),
  ('鐘聲', 16),
  ('酒店', 16),
  ('垃圾', 16),
  ('特首', 15),
  ('改革', 15),
  ('港澳', 15),
  ('縣', 15),
  ('貧困戶', 1